### Importing (and reimporting) a module

In [1]:
# places Python looks to import modules
import sys
sys.path

['/Users/dakoop/bin/miniforge3/envs/cs503/lib/python313.zip',
 '/Users/dakoop/bin/miniforge3/envs/cs503/lib/python3.13',
 '/Users/dakoop/bin/miniforge3/envs/cs503/lib/python3.13/lib-dynload',
 '',
 '/Users/dakoop/bin/miniforge3/envs/cs503/lib/python3.13/site-packages']

In [2]:
%%writefile my_module.py
def a():
    print("GOT HERE")

SECRET_NUMBER = 12

Writing my_module.py


In [3]:
# print contents of my_module.py
# function definition of a
# defining a constant SECRET_NUMBER
!cat my_module.py

def a():
    print("GOT HERE")

SECRET_NUMBER = 12


In [4]:
import my_module

In [5]:
dir(my_module)

['SECRET_NUMBER',
 '__builtins__',
 '__cached__',
 '__doc__',
 '__file__',
 '__loader__',
 '__name__',
 '__package__',
 '__spec__',
 'a']

In [6]:
my_module.SECRET_NUMBER

12

In [7]:
%%writefile my_module.py
def a():
    print("GOT HERE")

SECRET_NUMBER = 14

Overwriting my_module.py


In [8]:
# changed SECRET_NUMBER to 14
!cat my_module.py

def a():
    print("GOT HERE")

SECRET_NUMBER = 14


In [9]:
my_module.SECRET_NUMBER

12

In [10]:
import my_module

In [11]:
# this didn't change! imports are cached
my_module.SECRET_NUMBER

12

In [12]:
# reloading a module
import importlib
importlib.reload(my_module)

<module 'my_module' from '/Users/dakoop/Dropbox/Documents/Teaching/cs503-2025fa/notebooks/my_module.py'>

In [13]:
# now, we see the effect of the edit
import my_module
my_module.SECRET_NUMBER

14

In [14]:
my_module = importlib.import_module('.','.my_module')

<module '.my_module' from '/Users/dakoop/Dropbox/Documents/Teaching/cs503-2025fa/notebooks/my_module.py'>

In [22]:
importlib.reload(my_module)

<module '.my_module' from '/Users/dakoop/Dropbox/Documents/Teaching/cs503-2025fa/notebooks/my_module.py'>

In [33]:
import importlib
# import my_module2
import my_module
importlib.reload(my_module)
# importlib.reload(my_module2)

<module 'my_module' from '/Users/dakoop/Dropbox/Documents/Teaching/cs503-2025fa/notebooks/my_module.py'>

In [34]:
import my_module2

my_module2.b()

20


### Packages

In [35]:
%mkdir test_pkg

In [36]:
%%writefile test_pkg/foo.py
def flatten_list(a):
    return [x for xlist in a for x in xlist]

Writing test_pkg/foo.py


In [37]:
%%writefile test_pkg/bar.py
def list_diff(a):
    it1 = iter(a)
    it2 = iter(a)
    next(it2, None)
    return [b - a for a, b in zip(it1, it2)]

Writing test_pkg/bar.py


In [38]:
# print contents of test_pkg directory
# just two files foo.py and bar.py
!find test_pkg -type f -name "*.py" -not -path "*/.ipynb_checkpoints/*"

test_pkg/bar.py
test_pkg/foo.py


In [39]:
import test_pkg

In [40]:
dir(test_pkg)

['__doc__',
 '__file__',
 '__loader__',
 '__name__',
 '__package__',
 '__path__',
 '__spec__']

In [41]:
# this doesn't work because we didn't import test_pkg.foo
test_pkg.foo.flatten_list([[1,2],[3,4]])

AttributeError: module 'test_pkg' has no attribute 'foo'

In [42]:
import test_pkg.foo

In [43]:
test_pkg.foo.flatten_list([[1,2,3],[4,5]])

[1, 2, 3, 4, 5]

In [44]:
import test_pkg.bar

In [45]:
test_pkg.bar.list_diff([1,2,5,7])

[1, 3, 2]

In [46]:
from test_pkg.bar import list_diff

In [47]:
list_diff([3,6,9])

[3, 3]

#### \_\_init\_\_.py

In [48]:
%%writefile test_pkg/__init__.py
from . import foo
from . import bar

Writing test_pkg/__init__.py


In [49]:
import importlib
importlib.reload(test_pkg)

<module 'test_pkg' from '/Users/dakoop/Dropbox/Documents/Teaching/cs503-2025fa/notebooks/test_pkg/__init__.py'>

In [50]:
import test_pkg

In [51]:
# don't need to import test_pkg.foo now
# because __init__.py does it
test_pkg.foo.flatten_list([[1,2,3],[4,5]])

[1, 2, 3, 4, 5]

In [52]:
dir(test_pkg)

['__builtins__',
 '__cached__',
 '__doc__',
 '__file__',
 '__loader__',
 '__name__',
 '__package__',
 '__path__',
 '__spec__',
 'bar',
 'foo']

#### Subpackage

In [53]:
%mkdir test_pkg/baz

In [54]:
%%writefile test_pkg/baz/fun.py
def print_comma_list(a):
    print(', '.join(str(x) for x in a))

Writing test_pkg/baz/fun.py


In [55]:
%%writefile test_pkg/__init__.py
from . import foo
from . import bar
from .baz import fun

Overwriting test_pkg/__init__.py


In [56]:
import importlib
importlib.reload(test_pkg)

<module 'test_pkg' from '/Users/dakoop/Dropbox/Documents/Teaching/cs503-2025fa/notebooks/test_pkg/__init__.py'>

In [57]:
test_pkg.baz.fun.print_comma_list([1,2,3])

1, 2, 3


In [65]:
%%writefile test_pkg/__main__.py
import sys

from .baz import fun

if len(sys.argv) < 2:
    print("Usage: python -m test_pkg <list of integers>")
    sys.exit(0)
    
alist = [int(v) for v in sys.argv[1:]]
fun.print_comma_list(alist)

Overwriting test_pkg/__main__.py


In [66]:
!find test_pkg -type f -name "*.py" -not -path "*/.ipynb_checkpoints/*"

test_pkg/__init__.py
test_pkg/bar.py
test_pkg/baz/fun.py
test_pkg/__main__.py
test_pkg/foo.py


In [67]:
%run -m test_pkg

Usage: python -m test_pkg <list of integers>


In [68]:
%run -m test_pkg 12 34 25 3

12, 34, 25, 3


In [69]:
import test_pkg

In [70]:
test_pkg.fun

<module 'test_pkg.baz.fun' from '/Users/dakoop/Dropbox/Documents/Teaching/cs503-2025fa/notebooks/test_pkg/baz/fun.py'>

### Classses

In [71]:
class Vehicle:
    def __init__(self, make, model, year, color):
        self.make = make
        self.model = model
        self.year = year
        self.color = color

In [72]:
car1 = Vehicle('Honda', 'Accord', 2009, 'red')

In [73]:
car1

In [74]:
car2 = Vehicle('Dodge', 'Caravan', 2015, 'gray')

In [75]:
car2

In [78]:
car1.year, car1.model

(2009, 'Accord')

In [79]:
car2.year, car2.model

(2015, 'Caravan')

In [80]:
car2.year = 2016

In [81]:
car2.year, car2.model

(2016, 'Caravan')

In [82]:
class Vehicle:
    def __init__(self, make, model, year, color):
        self.make = make
        self.model = model
        self.year = year
        self.color = color

    def age(self):
        return 2025 - self.year
    
    def set_age(self, age):
        self.year = 2025 - age

In [83]:
car1 = Vehicle('Honda', 'Accord', 2009, 'red')

In [84]:
car1.set_age(43)

In [85]:
car1.age()

43

In [86]:
car1.year

1982

In [ ]:
car1.year = 1981

#### Visibility

In [87]:
class Vehicle:
    def __init__(self, make, model, year, color='gray'):
        self.make = make
        self.model = model
        self.year = year
        self.color = color
        self._color_hex = 'ff0000'
        self.__internal_vin = '23ab74f7e'

    def age(self):
        return 2025 - self.year

    def internal_vin(self):
        return self.__internal_vin

In [88]:
car1 = Vehicle('Honda', 'Accord', 2009, 'red')

In [89]:
car2 = Vehicle(color='blue', make='Ford', model='F150', year=2015)

In [90]:
car1.color

'red'

In [91]:
# this works
car1._color_hex = 'ffff00'

In [92]:
car1._color_hex

'ffff00'

In [93]:
# this doesn't
car1.__internal_vin

AttributeError: 'Vehicle' object has no attribute '__internal_vin'

In [94]:
# don't do this, but this is where it is
car1._Vehicle__internal_vin = '346782bc'

In [95]:
car1._Vehicle__internal_vin

'346782bc'

In [96]:
car1.internal_vin()

'346782bc'

In [97]:
car1.color

'red'